In [26]:
import pandas as pd
import json
from pandas.io.json import json_normalize
import numpy as np 
#for importing files
import glob, os
import matplotlib.pyplot as plt
%matplotlib inline
import csv
import math

#Library for hull calculation
from scipy.spatial import ConvexHull
import matplotlib.pyplot as plt
from matplotlib.path import Path
from scipy.spatial import distance


## Helper Methods

In [27]:
def SecsToGameTime(time):
    mins=(int(time)/60)
    secs=int(time)%60
    print (str(mins)+":"+str(secs))
    return str(mins)+":"+str(secs)

In [65]:
def GameTimetoSeconds(time):
    mins, secs = time.split(":")
    timeSecs = int(mins)*60+int(secs)
    #print(timeSecs)
    return timeSecs

#### Hull Calculation Helper Method

In [107]:
def getHull(moments, teamID):
    points = []
    
    if(int(moments[5][1][0]) == teamID):
        for positions in moments[5][1:6]:
            #print positions
            points.append([positions[2],positions[3]])
        print("Defensive positions: "+ str(points))
    else:
        for positions in moments[5][6:11]:
            #print positions
            points.append([positions[2],positions[3]])
        print("Defensive positions: "+str(points))
    
    np_points = np.asarray(points)
    np_points
    hull = ConvexHull(np_points)
    
    return hull,np_points

In [30]:
def distFromCentroid(hull, x,y):
        cx = np.mean(hull.points[hull.vertices,0])
        cy = np.mean(hull.points[hull.vertices,1])
        return ((x-cx)^2+(y-cy)^2)^.5

In [31]:
def isInHull(hull,np_points,x,y):
    #point in hull?
    hull_path = Path( np_points[hull.vertices] )
    isInPath = hull_path.contains_point((x,y))
    return (isInPath == True)

### Helper method for returning PBP descriptions given game and eventNum

In [59]:
def getPBPInfo(gameID,PBPEventNum):
    curPath = os.getcwd()
    if(not curPath.endswith('\pbp-csv')):
        curPath = os.getcwd()
        print curPath
        strIndex=curPath.index('\\JupyterNotebooks')
        curPath = curPath[:(strIndex+18)]+'\pbp-csv'
        os.chdir(curPath)
        print curPath
    
    events_df = pd.read_csv("00"+str(gameID)+".csv")
    eventRow = events_df[events_df['EVENTNUM'].isin([int(PBPEventNum)])]
     
    print eventRow['PCTIMESTRING']
    print eventRow['HOMEDESCRIPTION']
    print eventRow['VISITORDESCRIPTION']
    return eventRow['PCTIMESTRING'] , eventRow['HOMEDESCRIPTION'] , eventRow['VISITORDESCRIPTION']
    

### Given the game time (12:00) and eventNumber from the Play-by-play data for a recorded event, this method returns the correct eventNumber from the SportsVU data since they actually dont matchup.  This method converts the gametime into seconds (720s = 12:00) which is formatted in SportsVU.  It traverses up and down events until the gametime is within a selected eventNumber.

In [105]:
def findCorrectMomentData(rawSportVUData, quarterPBP, gametimePBP, approxEventNumPBP):
    print("Finding correct SportVU eventNum for gameid:"+rawSportVUData['gameid'])

    found = False;
    moments = None
    
    checkedValues = []
    
    prevEventNumPBP = None
    #convert gametimePBP (12:00) to seconds (720)
    gameInSeconds = GameTimetoSeconds(gametimePBP)
    while (found == False):
        print ("curr eventNum:"+str(approxEventNumPBP)+" , prev eventNum:"+ str(prevEventNumPBP))
        
        if(approxEventNumPBP in checkedValues):
            print("infinite loop")
            return None, None
        else:
            checkedValues.append(approxEventNumPBP)        
        
        print("Currently checking eventNumPBP: "+str(approxEventNumPBP))
        moments = MomentsfromEventNum(rawSportVUData, approxEventNumPBP)
        if (moments is None or len(moments) == 0):
            print("Could not find moments for this eventNum in SportsVU: "+ str(approxEventNumPBP))
            return None, None
        
        quarterSportVU = int(moments[0][0])
        print("Comparing Target PBP quarter:"+str(quarterPBP)+" , with  SportVU quarter :"+str(quarterSportVU))
        print("Comparing Target PBP gameclock:"+str(gameInSeconds)+" with SportsVU moment game clock:"+str(moments[0][2]))
        
        #check whether this EventNum moment is the correct time frame of the play from Play-by-play
        if(quarterPBP < quarterSportVU):
            approxEventNumPBP -= 1
        elif(quarterPBP > quarterSportVU):    
            approxEventNumPBP  += 1
            
        #is the PBP game time between the gametime of the moments extracted?
        elif(int(moments[0][2])+1 > gameInSeconds and int(moments[len(moments)-1][2])-1 < gameInSeconds):
            found=True
        elif(moments[0][2] < gameInSeconds):
            approxEventNumPBP -= 1
        elif(moments[len(moments)-1][2] > gameInSeconds):
        # look ahead 1 event 
            approxEventNumPBP += 1
        else:
            print("huge error, should not reach here")
            return None, None
        
    #the returned event num corresponds to SportsVU, which holds the time of the event we are looking for.... 
    print("Corrected eventNum to be searching for in SportsVU: "+ str(approxEventNumPBP))
    return approxEventNumPBP , moments

## Method returns the moments for the eventNum from PBP

In [34]:
def MomentsfromEventNum(eventsData, eventNumPBP):
    found = False
    searchDirection = None
    sportVUIndex = eventNumPBP
    eventsLen = len(eventsData['events'])-1
    if(eventsLen < sportVUIndex):
        sportVUIndex = eventsLen
    
    while(not found):        
        if( int(eventsData['events'][sportVUIndex]['eventId']) == eventNumPBP):
            found = True
        elif ( int(eventsData['events'][sportVUIndex]['eventId']) > eventNumPBP ):
            if(searchDirection is None and sportVUIndex > 0):
                searchDirection = "decrementIndex"
                sportVUIndex -= 1  
            elif(searchDirection is "decrementIndex" and sportVUIndex > 0):
                sportVUIndex -= 1  
            elif(searchDirection is "incrementIndex"):
                print("Failed finding eventnum in SportsVU, search directions switched.")
                return None
            else: #we have reached 0th index and cant traverse up the list anymore
                print("Failed finding eventnum in SportsVU")
                return None
        elif ( int(eventsData['events'][sportVUIndex]['eventId']) < eventNumPBP ):
            if(searchDirection is None and sportVUIndex < eventsLen):
                searchDirection = "incrementIndex"
                sportVUIndex += 1  
            elif(searchDirection is "incrementIndex" and sportVUIndex < eventsLen):
                sportVUIndex += 1  
            elif(searchDirection is "decrementIndex"):
                "Failed finding eventnum in SportsVU, search directions switched."
                return None
            else: #we have reached 0th index and cant traverse up the list anymore
                print("Failed finding eventnum in SportsVU")
                return None
    print("SportVU Index for the eventNumPBP: "+str(sportVUIndex))
    
    return (eventsData['events'][sportVUIndex]["moments"])

## Identify Moment of CATCH

1.  //sort events moment data from end time to beginning (reverse order)
timeballReceived, locationballReceived = getReceive (recieverID, List[Moments]) 

Each moment is taken every .25s, so the FIRST 8 moments (8 *.25 = 2 seconds) when the receiverID and ball are within (dist <= 1 ft), is when the ball was the moment before the ball was released.

reset numCount = 0;

Starting from this time, continue iterating through moments. If dist from receiver and ball >=1 ft, then this is time the ball was caught.

***separate calculation to check when the ball dist less than 1 ft for another teammate to determine if it was a pass in a certain amount of time (counted numCount)****

2.  Find "latest" instance when   distFrom ( Moment.Positions[0].x,Moment.Position[0].y , Moment.Position[ ??=playerID ].x , Moment.Position[ ??=playerID].y) <= 1ft )

   return the timemilis ,  position[0].x , position[0].y


In [118]:
 def getCatchEventDetails(receiverID, passerID, gametimePBP, moments):
    momentsReversed = moments[::-1]
    processComplete = False;
    indexBallCaught = None
    indexBallReleased = None
    finalIndex=0
    index=0
    found = False
    ball2receiver_distThreshold = 1 #if ball is < 1 feet from receiver, then he has it
    catchball2receiver_distThreshold = 2 # dist threshold for determining when the ball is caught has to be x ft away
    gameInSeconds = GameTimetoSeconds(gametimePBP)
    print("num of moments: "+str(len(momentsReversed)))
    while (found == False):
        #reverse the moment data, and 
        if(int(momentsReversed[index][2]) >=  gameInSeconds):
            found=True
        elif(int(momentsReversed[index][2]< gameInSeconds)):
            index += 1
        else:
            return "ERROR"
    
    print("starting at time: "+ str(momentsReversed[index][2])+ "with total momentList length of "+str(len(momentsReversed)))
    
    #Found the index of the approx start of the event
    numCounts=0
    for i in range(index,len(momentsReversed)):
       #Debug #print("Time of moment being checked"+ str(momentsReversed[i][2]))
       #Debug #print("current Index in momentList: "+ str(i))
        if numCounts >= 3:
            timeBallReleased = momentsReversed[i][2]
            #SecsToGameTime(timeBallReleased)  
            indexBallReleased = i
            break
        else:
            ball = momentsReversed[i][5][0]
            player_x = None
            player_y = None
            for positions in momentsReversed[i][5]:    
                if positions[1] == receiverID:
                    player_x = positions[2]
                    player_y = positions[3]
            
            if(player_x is None and player_y is None):
                print("couldnt find receiver in moment's position")
                continue
            else:
                dist = distance.euclidean([player_x,player_y],[ball[2],ball[3]])
                if dist <= ball2receiver_distThreshold:
                    print("receiver holding ball @ shotclock: " + str( momentsReversed[i][3]) + " @ gametime "+ str( momentsReversed[i][2] ))
                    numCounts += 1
    
    if(indexBallReleased is None):            
        print("Could not find when release occured, reached end of moment list and could not find when ball left receiver's hands")
        return None, None, None, None, None, None, None, None, None, None
    
    #count when ball is caught
    numCounts=0
    for j in range(indexBallReleased, len(momentsReversed)):
        if numCounts >= 3:
            timeBallCaught = momentsReversed[j][2]
            #SecsToGameTime(timeBallCaught)
            indexBallCaught = j
            
            #record position of receiver
            receiverMoment = momentsReversed[j][5]
            
            reciever_pos_x = None
            receiver_pos_y = None
            for positions in receiverMoment:
                if positions[1] == receiverID:
                    reciever_pos_x = positions[2]
                    receiver_pos_y = positions[3]
            
            if(reciever_pos_x is None and receiver_pos_y is None):
                continue
            
            receiverPosAtCaught = [reciever_pos_x, receiver_pos_y]
            print(receiverPosAtCaught)
            
            break
        else:
            ball = momentsReversed[j][5][0]
            player_x = None
            player_y = None
            for positions in momentsReversed[j][5]:
                if positions[1] == receiverID:
                    player_x = positions[2]
                    player_y = positions[3]
            
            #check if receiver was actually found in moment's positions
            if(player_x is None and player_y is None):
                continue
            else:
                dist = distance.euclidean([player_x,player_y],[ball[2],ball[3]])
                if dist >= 2:
                    print("receiver caught ball @ shotclock: " + str(momentsReversed[j][3])+" @ gametime " + str(momentsReversed[j][2]) + " received reversed index"+str(j))
                    #SecsToGameTime(momentsReversed[j][3])
                    numCounts += 1
            
            #if(momentsReversed[j][3] is None):       
            #    print("Couldnt find catch event")
            #   return None, None, None, None, None, None, None, None, None, None   
    
    #check if ball caught event in moments list
    if(indexBallCaught is None):      
        print("Couldnt find catch event")
        return None, None, None, None, None, None, None, None, None, None   
                
                
    #count when ball is passed
    numCounts=0
    for k in range(indexBallCaught, len(momentsReversed)):
        #Debug#print("Time of moment being checked"+ str(momentsReversed[k][2]))
        #Debug#print("current Index in momentList: "+ str(k))
        if numCounts >= 2:
            #Debug# print("passer passed ball @ shotclock: " +str(momentsReversed[k][3])+" @ gametime " + str(momentsReversed[k][2]))
            timeBallPassed = momentsReversed[k][2]
            indexBallPassed = k
            processComplete = True
               
            #record position of receiver
            receiverMoment = momentsReversed[k][5]
            receiverPos = [k for k in receiverMoment if receiverID in k]
            
            reciever_pos_x = receiverPos[0][2]
            receiver_pos_y = receiverPos[0][3]
            receiverPosAtPass = [reciever_pos_x ,receiver_pos_y]
        
            #record position of passer
            passerPos = [k for k in receiverMoment if passerID in k]
            
            passer_pos_x = passerPos[0][2]
            passer_pos_y = passerPos[0][3]
            passerPosAtPass = [passer_pos_x ,passer_pos_y]
            
            SportsVUReversedIndex = len(momentsReversed) - indexBallPassed
            
            break
        else:
            ball = momentsReversed[k][5][0]
            player_x = None
            player_y = None
            for positions in momentsReversed[k][5]:
                if positions[1] == passerID:
                    player_x = positions[2]
                    player_y = positions[3]
            if(player_x is None and player_y is None):
                continue
            else:
                dist = distance.euclidean([player_x,player_y],[ball[2],ball[3]])
                if dist <= 2:
                    #Debug#print("passer just passed ball @ shotclock " +str(momentsReversed[k][3])+" @ gametime " + str(momentsReversed[k][2]) + " passed reversed index" +str(k))
                    numCounts += 1
              
    if(not processComplete):
        print("Couldnt find pass event")
        return None, None, None, None, None, None, None, None, None , None
    
        
    return timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass, SportsVUReversedIndex 
   

## Get TO Event Info

In [36]:
 def getTOEventDetails(receiverID, passerID, defensiveTeamId, gametimePBP, moments):
    momentsReversed = moments[::-1]
    processComplete = False;
    indexBallCaught = None
    indexBallReleased = None
    finalIndex=0
    index=0
    found = False
    gameInSeconds = GameTimetoSeconds(gametimePBP)
    print("num of moments: "+str(len(momentsReversed)))
    while (found == False):
        if(int(momentsReversed[index][2]) >=  gameInSeconds):
            found=True
        elif(int(momentsReversed[index][2]< gameInSeconds)):
            index += 1
        else:
            return "ERROR"
    
    print("starting at time: "+ str(momentsReversed[index][2]))
    
    timeBallReleased = momentsReversed[index][2]
    indexBallReleased = index
    timeBallCaught = momentsReversed[index][2]
    timeBallPassed = momentsReversed[index][2]
    indexBallPassed = index
    indexBallCaught = index
 
    
    #record position of passer
    receiverMoment = momentsReversed[index][5]
    passerPos = [k for k in receiverMoment if passerID in k]
    if(len(passerPos) is 0):
        print("couldnt find passer")
        return None, None, None, None, None, None, None, None, None, None 

    passer_pos_x = passerPos[0][2]
    passer_pos_y = passerPos[0][3]
    passerPosAtPass = [passer_pos_x ,passer_pos_y]

    SportsVUReversedIndex = len(momentsReversed) - indexBallPassed
    
    
    #check if there is a receiver???
    if (receiverID is not 0):
        receiverPos = [k for k in receiverMoment if receiverID in k]
        if(len(receiverPos) is 0):
            print("couldnt find receiver")
            return None, None, None, None, None, None, None, None, None, None 
        reciever_pos_x = receiverPos[0][2]
        receiver_pos_y = receiverPos[0][3]
        receiverPosAtCaught = [reciever_pos_x, receiver_pos_y]
        receiverPosAtPass = [reciever_pos_x, receiver_pos_y]
    else:
        receiverPosAtPass = [0,0]
        receiverPosAtCaught = [0,0]
        
     
    return timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass, SportsVUReversedIndex 
   

### Is receiving player open calculation

In [37]:
import math
# is_open
#   determines whether a player is "open" based on distance of nearest defender
#   note that the moment that the player shoots isn't determined in this function
# Params:
#   shooter_loc: location of the shooter at a given moment as a tuple (x, y)
#   def_locs: locations of each defender as list of tuples (x, y)
def is_open(shooter_loc, def_locs):

    dists = []
    for loc in def_locs:
        dist = math.hypot(shooter_loc[0] - loc[0], shooter_loc[1] - loc[1])
        if dist < 5:
            return dist, False
        dists.append(dist)
    dists = sorted(dists)
    return dists[0], True

shooter_loc = (6, 30)
#def_locs = [(56.27694, 25.51460), (73.64107, 25.48774), (48.6492, 35.26915), (48.46352, 14.55436), (47.51449, 24.36448)]
def_locs = [[37.42557, 15.22122], [5.85435, 29.07262], [31.67908, 38.87012], [45.11946, 31.22009], [12.7611, 43.81261]]
print(is_open(shooter_loc, def_locs))

(0.9387478825009401, False)


### Extracts Assists, Bad Passes, Alley Oops from csvs in current directory and saves them into separate csv files

In [127]:
AST_df = pd.DataFrame()
BadPass_df = pd.DataFrame()
AlleyOop_df = pd.DataFrame()
curPath = os.getcwd()
print curPath
if(not curPath.endswith('\pbp-csv')):
    curPath = os.getcwd()
    print curPath
    strIndex=curPath.index('\\JupyterNotebooks')
    curPath = curPath[:(strIndex+18)]+'\pbp-csv'
    os.chdir(curPath)
    print curPath
for pbpFile in glob.glob("*.csv"):
    print(pbpFile)
    #read file as df
    events_df = pd.read_csv(pbpFile)
    ASTList = events_df[events_df['EVENTMSGTYPE'].isin([1,2]) & ( events_df['VISITORDESCRIPTION'].str.contains("AST", na = False ) | events_df['HOMEDESCRIPTION'].str.contains("AST", na = False )  ) ]
    BadPassList= events_df[( events_df['VISITORDESCRIPTION'].str.contains("Bad", na = False ) | events_df['HOMEDESCRIPTION'].str.contains("Bad", na = False )  ) ]
    AlleyOopList= events_df[events_df['EVENTMSGTYPE'].isin([1,2]) & ( events_df['VISITORDESCRIPTION'].str.contains("Alley", na = False ) | events_df['HOMEDESCRIPTION'].str.contains("Alley", na = False )  ) ]
    AST_df = AST_df.append(ASTList)
    BadPass_df = BadPass_df.append(BadPassList)
    AlleyOop_df = AlleyOop_df.append(AlleyOopList)
    
AST_df.to_csv("AST_Parsed.csv", sep='\t')
BadPass_df.to_csv("BadPass_Parsed.csv", sep='\t')
AlleyOop_df.to_csv("AlleyOop_Parsed.csv", sep='\t')

C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\\pbp-csv
0021500001.csv
0021500002.csv
0021500003.csv
0021500004.csv
0021500005.csv
0021500007.csv
0021500009.csv
0021500010.csv
0021500011.csv
0021500012.csv
0021500013.csv
0021500015.csv
0021500016.csv
0021500017.csv
0021500018.csv
0021500019.csv
0021500020.csv
0021500021.csv
0021500022.csv
0021500023.csv
0021500024.csv
0021500025.csv
0021500026.csv
0021500027.csv
0021500028.csv
0021500029.csv
0021500031.csv
0021500032.csv
0021500033.csv
0021500034.csv
0021500035.csv
0021500036.csv
0021500037.csv
0021500038.csv
0021500039.csv
0021500040.csv
0021500041.csv
0021500042.csv
0021500043.csv
0021500044.csv
0021500045.csv
0021500046.csv
0021500047.csv
0021500048.csv
0021500049.cs

In [48]:
def moments2JSON(moment):
    json = "{"
    json += " \"period\" :"+str(moment[0])+","
    json += " \"Unixtime\" :"+str(moment[1])+","
    json += " \"secondsRemaining\" :"+str(moment[2])+","
    json += " \"shotClock\" :"+str(moment[3])+","
    json += " \"misc\" : \""+str(moment[4])+"\","
    json += " \"positions\" :"+"["
    
    a=[]
    for positions in moment[5]:
        a.append("{ \"teamid\":"+str(positions[0])+", \"playerid\":"+str(positions[1])+", \"x\":"+str(positions[2])+", \"y\":"+str(positions[3])+", \"z\":"+str(positions[4])+"}")
        myString = ",".join(a)
    json += myString +"]}"
    return json

convertedJSON = moments2JSON(momentsReversed[1])
print convertedJSON
#a= "{
#    "period" : momentsReversed[0],
#    "Unixtime": momentsReversed[1],
#    "secondsRemaining": momentsReversed[2],
#    "shotClock": momentsReversed[3],
 #   "misc": momentsReversed[4],
#    "Unixtime": momentsReversed[5]  
#}"

#print myString

{ "period" :3, "Unixtime" :1446409845949, "secondsRemaining" :280.28, "shotClock" :17.31, "misc" : "None", "positions" :[{ "teamid":-1, "playerid":-1, "x":62.26333, "y":15.76904, "z":4.63954},{ "teamid":1610612766, "playerid":2744, "x":83.89182, "y":21.83319, "z":0.0},{ "teamid":1610612766, "playerid":101107, "x":68.26152, "y":25.68091, "z":0.0},{ "teamid":1610612766, "playerid":201587, "x":80.50109, "y":23.45231, "z":0.0},{ "teamid":1610612766, "playerid":202689, "x":68.50319, "y":15.452, "z":0.0},{ "teamid":1610612766, "playerid":203798, "x":70.70026, "y":33.49793, "z":0.0},{ "teamid":1610612737, "playerid":2594, "x":62.56446, "y":13.52911, "z":0.0},{ "teamid":1610612737, "playerid":200794, "x":83.98771, "y":27.23136, "z":0.0},{ "teamid":1610612737, "playerid":201143, "x":60.04235, "y":24.94316, "z":0.0},{ "teamid":1610612737, "playerid":201168, "x":84.96276, "y":16.45598, "z":0.0},{ "teamid":1610612737, "playerid":201952, "x":61.16716, "y":40.08791, "z":0.0}]}


## AST_df  assists data frame has time and event num of all assists....

In [ ]:
AST_df

In [128]:
# for each assist event 
print("Starting unparsed pass dataset: "+ str(len(AST_df)))
CleanData_df = pd.DataFrame(columns=['GameID', 'Period', 'SportVUeventNum', 'SportVUMomentIndex', 'reversedIndexBallCaught', 'PBPGameTime' , 'timeballpassed','timeballcaught', 'ShotClock', 'PasserID', 'ReceiverID', 'PassDist',  'passInHull', 'receiverinHull', 'HullArea','receiverIsOpen' , 'PBP_HOMEDESCRIPTION' , 'PBP_VISITORDESCRIPTION', 'rawMoments', 'defensivePositions', 'isAlleyOOp', 'Success'])
momentsJson_df = pd.DataFrame(columns=['jsonMoments'])
if(not curPath.endswith('SportVU_JSON_Data')):
    curPath = os.getcwd()
    print curPath
    strIndex=curPath.index('\\JupyterNotebooks\\')
    curPath = curPath[:(strIndex+18)]+'SportVU_JSON_Data\\'
    os.chdir(curPath)
print curPath
#SportVU_JSON_Rootpath = "C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\\"
#print SportVU_JSON_Rootpath+str(gameid)+".json"
gameid_prev = 0;
for index, ast in AST_df.iterrows():
    gameid = ast["GAME_ID"]    #game id from PBP
    eventNumPBP = ast["EVENTNUM"] #eventNumber for the play
    gametimePBP = ast["PCTIMESTRING"]  #game time for the play
    quarterPBP = int(ast["PERIOD"])
    #getPBPInfo(gameid,eventNumPBP)
    print("prevGameID:"+str(gameid_prev)+", currentlyAnalyzingGameID:"+str(gameid))
    print("PBPEventNum:"+str(eventNumPBP)+", gametimePBP:"+str(gametimePBP)+"\n")
    #check if SportVU json data is already opened for this PBP play
    if(gameid_prev != gameid):
        #open raw JSON SportVU data using game id from assist
        with open(curPath+"00"+str(gameid)+".json") as data_file:    
            rawSportVUData = json.load(data_file)
            json_normalize(rawSportVUData['events'])
        gameid_prev = gameid
    
    #get the correct eventNum (returned as long) in SportsVU and moments Data
    eventNumSportsVU, rawpossessionSportsVU = findCorrectMomentData(rawSportVUData, quarterPBP, gametimePBP, eventNumPBP)
    if(eventNumSportsVU is None):
        print("Could not find eventNum in SportsVU \n")
        continue
 
    #for analyzing AST only...
    receiverID = int(ast['PLAYER1_ID'])
    print()
    passerID = int(ast['PLAYER2_ID'])
    print("receiverID = "+str(receiverID)+ " , passerID = "+str(passerID))
    teamID = int(ast['PLAYER1_TEAM_ID'])
    #PBPTime = str(ast['PCTIMESTRING'])
    PBP_HOMEDESCRIPTION = str(ast['HOMEDESCRIPTION']) 
    PBP_VISITORDESCRIPTION = str(ast['VISITORDESCRIPTION'])
    if("nan" not in PBP_HOMEDESCRIPTION):
        print (PBP_HOMEDESCRIPTION)
    else: print(PBP_VISITORDESCRIPTION)
                     
    #get catch details (who was the passer, receiver, and when caught/passed)
    timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass , SportVUMomentIndex= getCatchEventDetails(receiverID, passerID, gametimePBP, rawpossessionSportsVU)
    
    if(timeBallReleased is None):
        print("Could not find time for when ball was passed \n")
        continue
    
    #hull details
    momentsReversed = rawpossessionSportsVU[::-1]
    
    if (rawSportVUData['events'][0]['home']['teamid'] == teamID ):
        print("defense team: "+rawSportVUData['events'][0]['visitor']['name']);
        defenseTeamId =  rawSportVUData['events'][0]['visitor']['teamid'];
    else:
        defenseTeamId =  rawSportVUData['events'][0]['home']['teamid'];
        print("Defense team: "+rawSportVUData['events'][0]['home']['name']);
    hull, defensive_positions = getHull(momentsReversed[indexBallCaught], defenseTeamId)
    
    #Defensive Hull Area
    hullArea = hull.area
    
    #passer in hull?
    passerInHull = isInHull(hull,defensive_positions, passerPosAtPass[0] ,passerPosAtPass[1])
                     
    #receiver in hull?
    receiverInHull = isInHull(hull,defensive_positions, receiverPosAtPass[0] ,receiverPosAtPass[1])
      
    #is receiver open?  ( np_points position of defense)
    closestDist, receiverIsOpen = is_open([receiverPosAtCaught[0],receiverPosAtCaught[1]], defensive_positions)
    
    #pass Distance
    passDist =distance.euclidean(passerPosAtPass,receiverPosAtCaught)
    
    #shot clock time
    shotClockTime = momentsReversed[indexBallPassed][3]
    
    rawMoments =  momentsReversed[indexBallCaught:indexBallPassed]
    #unreverse moments
    rawMoments = rawMoments[::-1]
        
    isAlleyOop = False;
    isSuccess = True;
    
    #PBPTime , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION = getPBPInfo("00"+str(gameid), eventNumPBP) 
    CleanData_df.loc[len(CleanData_df.index)] = [gameid, quarterPBP, eventNumSportsVU, SportVUMomentIndex , indexBallCaught, gametimePBP, timeBallPassed, timeBallCaught, shotClockTime, passerID, receiverID , passDist, passerInHull, receiverInHull, hullArea, receiverIsOpen  , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION, rawMoments, defensive_positions, isAlleyOop,  isSuccess]
    #momentsJson_df.loc[len(momentsJson_df.index)] = [jsonMoments]
    
CleanData_df.to_csv("CleanedDataRegAST_.csv", sep=',')
#momentsJson_df.to_csv("momentdataonly.csv", sep=' ', index=False, header=False)


Starting unparsed pass dataset: 4114
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\pbp-csv
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\
prevGameID:0, currentlyAnalyzingGameID:21500001
PBPEventNum:5, gametimePBP:11:21

Finding correct SportVU eventNum for gameid:0021500001
curr eventNum:5 , prev eventNum:None
Currently checking eventNumPBP: 5
sportVU Index for the eventNumPBP: 4
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:681 with SportsVU moment game clock:697.0
Corrected eventNum to be searching for in SportsVU: 5
()
receiverID = 202694 , passerID = 203083
Marc Morris 13' Step Back Jump Shot (2 PTS) (Drummond 1 AST)
num of moments: 623
starting at time: 681.02with total momentList length of 623
receiver holding ball @ shotclock: 9.71 @ gametime 683.49
receiver holding ball @ shotclock: 9.75 @ gametime 683.53
receiver holding b

prevGameID:21500001, currentlyAnalyzingGameID:21500001
PBPEventNum:269, gametimePBP:8:37

Finding correct SportVU eventNum for gameid:0021500001
curr eventNum:269 , prev eventNum:None
Currently checking eventNumPBP: 269
sportVU Index for the eventNumPBP: 243
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:517 with SportsVU moment game clock:532.0
Corrected eventNum to be searching for in SportsVU: 269
()
receiverID = 203484 , passerID = 203083
Caldwell-Pope 19' Pullup Jump Shot (12 PTS) (Drummond 3 AST)
num of moments: 514
starting at time: 517.01with total momentList length of 514
receiver holding ball @ shotclock: 8.99 @ gametime 517.29
receiver holding ball @ shotclock: 9.03 @ gametime 517.33
receiver holding ball @ shotclock: 9.07 @ gametime 517.37
receiver caught ball @ shotclock: 9.56 @ gametime 517.85 received reversed index33
receiver caught ball @ shotclock: 9.6 @ gametime 517.89 received reversed index34
receiver caught ball @ shotcloc

prevGameID:21500001, currentlyAnalyzingGameID:21500001
PBPEventNum:455, gametimePBP:4:27

Finding correct SportVU eventNum for gameid:0021500001
curr eventNum:455 , prev eventNum:None
Currently checking eventNumPBP: 455
sportVU Index for the eventNumPBP: 399
Comparing Target PBP quarter:4 , with  SportVU quarter :4
Comparing Target PBP gameclock:267 with SportsVU moment game clock:275.88
Corrected eventNum to be searching for in SportsVU: 455
()
receiverID = 2594 , passerID = 201952
Korver 25' 3PT Pullup Jump Shot (5 PTS) (Teague 4 AST)
num of moments: 350
starting at time: 267.02with total momentList length of 350
receiver holding ball @ shotclock: 16.69 @ gametime 269.41
receiver holding ball @ shotclock: 16.73 @ gametime 269.45
receiver holding ball @ shotclock: 16.77 @ gametime 269.49
receiver caught ball @ shotclock: 18.39 @ gametime 271.1 received reversed index227
receiver caught ball @ shotclock: 18.43 @ gametime 271.14 received reversed index228
receiver caught ball @ shotcloc

prevGameID:21500002, currentlyAnalyzingGameID:21500002
PBPEventNum:286, gametimePBP:0:23

Finding correct SportVU eventNum for gameid:0021500002
curr eventNum:286 , prev eventNum:None
Currently checking eventNumPBP: 286
sportVU Index for the eventNumPBP: 251
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:23 with SportsVU moment game clock:33.01
Corrected eventNum to be searching for in SportsVU: 286
()
receiverID = 203926 , passerID = 201149
McDermott 17' Driving Floating Jump Shot (7 PTS) (Noah 2 AST)
num of moments: 800
starting at time: 23.01with total momentList length of 800
receiver holding ball @ shotclock: 15.37 @ gametime 26.89
receiver holding ball @ shotclock: 15.41 @ gametime 26.93
receiver holding ball @ shotclock: 15.44 @ gametime 26.97
receiver caught ball @ shotclock: 15.95 @ gametime 27.53 received reversed index662
receiver caught ball @ shotclock: 15.99 @ gametime 27.57 received reversed index663
receiver caught ball @ shotcl

Finding correct SportVU eventNum for gameid:0021500003
curr eventNum:4 , prev eventNum:None
Currently checking eventNumPBP: 4
sportVU Index for the eventNumPBP: 3
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:695 with SportsVU moment game clock:711.22
Corrected eventNum to be searching for in SportsVU: 4
()
receiverID = 203110 , passerID = 202691
Green 26' 3PT Jump Shot (3 PTS) (Thompson 1 AST)
num of moments: 450
starting at time: 695.01with total momentList length of 450
receiver holding ball @ shotclock: 14.41 @ gametime 709.41
Could not find when release occured, reached end of moment list and could not find when ball left receiver's hands
Could not find time for when ball was passed 

prevGameID:21500003, currentlyAnalyzingGameID:21500003
PBPEventNum:5, gametimePBP:11:18

Finding correct SportVU eventNum for gameid:0021500003
curr eventNum:5 , prev eventNum:None
Currently checking eventNumPBP: 5
sportVU Index for the eventNumPBP: 4
Compar

...

prevGameID:21500098, currentlyAnalyzingGameID:21500098
PBPEventNum:294, gametimePBP:7:35

Finding correct SportVU eventNum for gameid:0021500098
curr eventNum:294 , prev eventNum:None
Currently checking eventNumPBP: 294
sportVU Index for the eventNumPBP: 250
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:455 with SportsVU moment game clock:474.29
Corrected eventNum to be searching for in SportsVU: 294
()
receiverID = 203083 , passerID = 202704
Drummond 7' Hook Shot (18 PTS) (Jackson 2 AST)
num of moments: 575
starting at time: 455.01with total momentList length of 575
receiver holding ball @ shotclock: 11.47 @ gametime 457.85
receiver holding ball @ shotclock: 11.51 @ gametime 457.89
receiver holding ball @ shotclock: 11.54 @ gametime 457.93
receiver caught ball @ shotclock: 11.69 @ gametime 458.09 received reversed index169
receiver caught ball @ shotclock: 11.73 @ gametime 458.13 received reversed index170
receiver caught ball @ shotclock: 11

Couldnt find pass event
Could not find time for when ball was passed 

prevGameID:21500098, currentlyAnalyzingGameID:21500098
PBPEventNum:544, gametimePBP:0:29

Finding correct SportVU eventNum for gameid:0021500098
curr eventNum:544 , prev eventNum:None
Currently checking eventNumPBP: 544
sportVU Index for the eventNumPBP: 445
Comparing Target PBP quarter:4 , with  SportVU quarter :4
Comparing Target PBP gameclock:29 with SportsVU moment game clock:47.05
Corrected eventNum to be searching for in SportsVU: 544
()
receiverID = 201229 , passerID = 202704
Tolliver  3PT Jump Shot (6 PTS) (Jackson 5 AST)
num of moments: 575
starting at time: 29.04with total momentList length of 575
receiver holding ball @ shotclock: 8.88 @ gametime 31.09
receiver holding ball @ shotclock: 8.94 @ gametime 31.14
receiver holding ball @ shotclock: 8.98 @ gametime 31.18
receiver caught ball @ shotclock: 9.59 @ gametime 31.81 received reversed index193
receiver caught ball @ shotclock: 9.63 @ gametime 31.85 rece

prevGameID:21500099, currentlyAnalyzingGameID:21500099
PBPEventNum:139, gametimePBP:10:00

Finding correct SportVU eventNum for gameid:0021500099
curr eventNum:139 , prev eventNum:None
Currently checking eventNumPBP: 139
sportVU Index for the eventNumPBP: 126
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:600 with SportsVU moment game clock:607.01
Corrected eventNum to be searching for in SportsVU: 139
()
receiverID = 1626167 , passerID = 201155
Turner 13' Turnaround Jump Shot (2 PTS) (Stuckey 1 AST)
num of moments: 425
starting at time: 600.01with total momentList length of 425
receiver holding ball @ shotclock: 16.45 @ gametime 602.25
receiver holding ball @ shotclock: 16.48 @ gametime 602.29
receiver holding ball @ shotclock: 16.52 @ gametime 602.33
receiver caught ball @ shotclock: 16.85 @ gametime 602.69 received reversed index316
receiver caught ball @ shotclock: 17.49 @ gametime 603.37 received reversed index333
receiver caught ball @ sh

prevGameID:21500099, currentlyAnalyzingGameID:21500099
PBPEventNum:309, gametimePBP:5:05

Finding correct SportVU eventNum for gameid:0021500099
curr eventNum:309 , prev eventNum:None
Currently checking eventNumPBP: 309
sportVU Index for the eventNumPBP: 278
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:305 with SportsVU moment game clock:314.77
Corrected eventNum to be searching for in SportsVU: 309
()
receiverID = 101139 , passerID = 202331
Miles 26' 3PT Jump Shot (9 PTS) (George 4 AST)
num of moments: 475
starting at time: 305.01with total momentList length of 475
receiver holding ball @ shotclock: 14.57 @ gametime 307.65
receiver holding ball @ shotclock: 14.61 @ gametime 307.69
receiver holding ball @ shotclock: 14.64 @ gametime 307.73
receiver caught ball @ shotclock: 15.1 @ gametime 308.29 received reversed index312
receiver caught ball @ shotclock: 15.14 @ gametime 308.33 received reversed index313
receiver caught ball @ shotclock: 15.

prevGameID:21500099, currentlyAnalyzingGameID:21500099
PBPEventNum:477, gametimePBP:1:42

Finding correct SportVU eventNum for gameid:0021500099
curr eventNum:477 , prev eventNum:None
Currently checking eventNumPBP: 477
sportVU Index for the eventNumPBP: 421
Comparing Target PBP quarter:4 , with  SportVU quarter :4
Comparing Target PBP gameclock:102 with SportsVU moment game clock:112.94
Corrected eventNum to be searching for in SportsVU: 477
()
receiverID = 203095 , passerID = 203901
Fournier 26' 3PT Jump Shot (21 PTS) (Payton 7 AST)
num of moments: 534
starting at time: 102.02with total momentList length of 534
receiver holding ball @ shotclock: 12.93 @ gametime 104.23
receiver holding ball @ shotclock: 12.97 @ gametime 104.27
receiver holding ball @ shotclock: 13.0 @ gametime 104.31
receiver caught ball @ shotclock: 13.53 @ gametime 104.87 received reversed index331
receiver caught ball @ shotclock: 13.56 @ gametime 104.91 received reversed index332
receiver caught ball @ shotclock:

## Mining each alleyOop event 

In [129]:
print("Starting unparsed pass dataset: "+ str(len(AlleyOop_df)))
CleanData_df = pd.DataFrame(columns=['GameID', 'Period', 'SportVUeventNum', 'SportVUMomentIndex', 'reversedIndexBallCaught', 'PBPGameTime' , 'timeballpassed','timeballcaught', 'ShotClock', 'PasserID', 'ReceiverID', 'PassDist',  'passInHull', 'receiverinHull', 'HullArea','receiverIsOpen' , 'PBP_HOMEDESCRIPTION' , 'PBP_VISITORDESCRIPTION', 'rawMoments', 'defensivePositions', 'isAlleyOOp', 'Success'])
momentsJson_df = pd.DataFrame(columns=['jsonMoments'])
if(not curPath.endswith('SportVU_JSON_Data')):
    curPath = os.getcwd()
    print curPath
    strIndex=curPath.index('\\JupyterNotebooks\\')
    curPath = curPath[:(strIndex+18)]+'SportVU_JSON_Data\\'
    os.chdir(curPath)
print curPath
#SportVU_JSON_Rootpath = "C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\\"
#print SportVU_JSON_Rootpath+str(gameid)+".json"
gameid_prev = 0;
for index, oop in AlleyOop_df.iterrows():
    gameid = oop["GAME_ID"]    #game id from PBP
    eventNumPBP = oop["EVENTNUM"] #eventNumber for the play
    gametimePBP = oop["PCTIMESTRING"]  #game time for the play
    quarterPBP = int(oop["PERIOD"])
    #getPBPInfo(gameid,eventNumPBP)
    print("prevGameID:"+str(gameid_prev)+", currentlyAnalyzingGameID:"+str(gameid))
    print("PBPEventNum:"+str(eventNumPBP)+", gametimePBP:"+str(gametimePBP))
    #check if SportVU json data is already opened for this PBP play
    if(gameid_prev != gameid):
        #open raw JSON SportVU data using game id from assist
        with open(curPath+"00"+str(gameid)+".json") as data_file:    
            rawSportVUData = json.load(data_file)
            json_normalize(rawSportVUData['events'])
        gameid_prev = gameid
    
    #get the correct eventNum (returned as long) in SportsVU and moments Data
    eventNumSportsVU, rawpossessionSportsVU = findCorrectMomentData(rawSportVUData, quarterPBP, gametimePBP, eventNumPBP)
    if(eventNumSportsVU is None):
        print("Could not find eventNum in SportsVU \n")
        continue
    
    
    print("Correct SportVU eventNum: "+str(eventNumSportsVU))
    #extract SportsVU movements for that eventNum
    
    #rawpossessionSportsVU = MomentsfromEventNum(rawSportVUData, int(eventNumSportsVU))   
    
    #for analyzing OOP only...
    receiverID = int(oop['PLAYER1_ID'])
    passerID = int(oop['PLAYER2_ID'])
    print("receiverID = "+str(receiverID)+ " , passerID = "+str(passerID))
    teamID = int(oop['PLAYER1_TEAM_ID'])
    #PBPTime = str(oop['PCTIMESTRING'])
    PBP_HOMEDESCRIPTION = str(oop['HOMEDESCRIPTION']) 
    PBP_VISITORDESCRIPTION = str(oop['VISITORDESCRIPTION'])
    if("nan" not in PBP_HOMEDESCRIPTION):
        print (PBP_HOMEDESCRIPTION)
    else: print(PBP_VISITORDESCRIPTION)

                     
    #get catch details (who was the passer, receiver, and when caught/passed)
    timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass , SportVUMomentIndex= getCatchEventDetails(receiverID, passerID, gametimePBP, rawpossessionSportsVU)
    
    if(timeBallReleased is None):
        print("Could not find time for when ball was passed")
        continue
    
    #hull details
    momentsReversed = rawpossessionSportsVU[::-1]
    
    if (rawSportVUData['events'][0]['home']['teamid'] == teamID ):
        print("defense team: "+rawSportVUData['events'][0]['visitor']['name']);
        defenseTeamId =  rawSportVUData['events'][0]['visitor']['teamid'];
    else:
        defenseTeamId =  rawSportVUData['events'][0]['home']['teamid'];
        print("defense team: "+rawSportVUData['events'][0]['home']['name']);
    hull, defensive_positions = getHull(momentsReversed[indexBallCaught], defenseTeamId)
    
    #Defensive Hull Area
    hullArea = hull.area
    
    #passer in hull?
    passerInHull = isInHull(hull,defensive_positions, passerPosAtPass[0] ,passerPosAtPass[1])
                     
    #receiver in hull?
    receiverInHull = isInHull(hull,defensive_positions, receiverPosAtPass[0] ,receiverPosAtPass[1])
      
    #is receiver open?  ( np_points position of defense)
    closestDist, receiverIsOpen = is_open([receiverPosAtCaught[0],receiverPosAtCaught[1]], defensive_positions)
    
    #pass Distance
    passDist =distance.euclidean(passerPosAtPass,receiverPosAtCaught)
    
    #shot clock time
    shotClockTime = momentsReversed[indexBallPassed][3]
    
    rawMoments =  momentsReversed[indexBallCaught:indexBallPassed]
    #unreverse moments
    rawMoments = rawMoments[::-1] 
    
    isAlleyOop = True;
    if("nan" not in PBP_HOMEDESCRIPTION):
        if("MISS" not in PBP_HOMEDESCRIPTION):
            isSuccess = True;
        else:
            isSuccess = False;
    else: 
        if("MISS" not in PBP_VISITORDESCRIPTION):
            isSuccess = True;
        else:
            isSuccess = False;
    
    #PBPTime , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION = getPBPInfo("00"+str(gameid), eventNumPBP) 
    CleanData_df.loc[len(CleanData_df.index)] = [gameid, quarterPBP, eventNumSportsVU, SportVUMomentIndex , indexBallCaught, gametimePBP, timeBallPassed, timeBallCaught, shotClockTime, passerID, receiverID , passDist, passerInHull, receiverInHull, hullArea, receiverIsOpen  , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION, rawMoments, defensive_positions, isAlleyOop,  isSuccess]
    #momentsJson_df.loc[len(momentsJson_df.index)] = [jsonMoments]
    
CleanData_df.to_csv("CleanedDataOOP_Successful_.csv", sep=',')
#momentsJson_df.to_csv("momentdataonly.csv", sep=' ', index=False, header=False)


Starting unparsed pass dataset: 175
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\
prevGameID:0, currentlyAnalyzingGameID:21500001
PBPEventNum:86, gametimePBP:3:33
Finding correct SportVU eventNum for gameid:0021500001
curr eventNum:86 , prev eventNum:None
Currently checking eventNumPBP: 86
sportVU Index for the eventNumPBP: 75
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:213 with SportsVU moment game clock:223.09
Corrected eventNum to be searching for in SportsVU: 86
Correct SportVU eventNum: 86
receiverID = 203083 , passerID = 202704
Drummond  Alley Oop Layup (4 PTS) (Jackson 3 AST)
num of moments: 350
starting at time: 213.03with total momentList length of 350
receiver holding ball @ shotclock: 16.01 @ gametime 215.87
receiver holding ball @ shotclock: 16.05 @ game

Finding correct SportVU eventNum for gameid:0021500007
curr eventNum:27 , prev eventNum:None
Currently checking eventNumPBP: 27
sportVU Index for the eventNumPBP: 26
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:467 with SportsVU moment game clock:476.83
Corrected eventNum to be searching for in SportsVU: 27
Correct SportVU eventNum: 27
receiverID = 203497 , passerID = 203526
Gobert 1' Alley Oop Layup (2 PTS) (Neto 2 AST)
num of moments: 400
starting at time: 467.03with total momentList length of 400
Could not find when release occured, reached end of moment list and could not find when ball left receiver's hands
Could not find time for when ball was passed
prevGameID:21500007, currentlyAnalyzingGameID:21500007
PBPEventNum:318, gametimePBP:2:28
Finding correct SportVU eventNum for gameid:0021500007
curr eventNum:318 , prev eventNum:None
Currently checking eventNumPBP: 318
sportVU Index for the eventNumPBP: 288
Comparing Target PBP quarter:3 , 

Finding correct SportVU eventNum for gameid:0021500013
curr eventNum:435 , prev eventNum:None
Currently checking eventNumPBP: 435
sportVU Index for the eventNumPBP: 363
Comparing Target PBP quarter:4 , with  SportVU quarter :4
Comparing Target PBP gameclock:524 with SportsVU moment game clock:543.98
Corrected eventNum to be searching for in SportsVU: 435
Correct SportVU eventNum: 435
receiverID = 203500 , passerID = 201571
Adams  Alley Oop Dunk (6 PTS) (Augustin 4 AST)
num of moments: 575
starting at time: 524.02with total momentList length of 575
receiver holding ball @ shotclock: 23.29 @ gametime 524.91
receiver holding ball @ shotclock: 10.81 @ gametime 526.48
receiver holding ball @ shotclock: 10.84 @ gametime 526.52
receiver caught ball @ shotclock: 11.1 @ gametime 526.84 received reversed index148
receiver caught ball @ shotclock: 11.14 @ gametime 526.88 received reversed index149
receiver caught ball @ shotclock: 11.17 @ gametime 526.92 received reversed index150
[83.15955, 27.2

Finding correct SportVU eventNum for gameid:0021500021
curr eventNum:121 , prev eventNum:None
Currently checking eventNumPBP: 121
sportVU Index for the eventNumPBP: 94
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:112 with SportsVU moment game clock:110.1
curr eventNum:120 , prev eventNum:None
Currently checking eventNumPBP: 120
sportVU Index for the eventNumPBP: 93
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:112 with SportsVU moment game clock:128.09
Corrected eventNum to be searching for in SportsVU: 120
Correct SportVU eventNum: 120
receiverID = 202684 , passerID = 203521
Thompson  Alley Oop Dunk (2 PTS) (Dellavedova 1 AST)
num of moments: 600
starting at time: 112.02with total momentList length of 600
Could not find when release occured, reached end of moment list and could not find when ball left receiver's hands
Could not find time for when ball was passed
prevGameID:21500021, currentlyAnalyzi

Finding correct SportVU eventNum for gameid:0021500025
curr eventNum:57 , prev eventNum:None
Currently checking eventNumPBP: 57
sportVU Index for the eventNumPBP: 53
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:375 with SportsVU moment game clock:387.0
Corrected eventNum to be searching for in SportsVU: 57
Correct SportVU eventNum: 57
receiverID = 203083 , passerID = 202704
Drummond  Alley Oop Dunk (4 PTS) (Jackson 2 AST)
num of moments: 806
starting at time: 375.02with total momentList length of 806
receiver holding ball @ shotclock: 15.21 @ gametime 379.14
receiver holding ball @ shotclock: 15.25 @ gametime 379.18
receiver holding ball @ shotclock: 15.3 @ gametime 379.22
receiver caught ball @ shotclock: 15.61 @ gametime 379.5 received reversed index491
receiver caught ball @ shotclock: 15.65 @ gametime 379.54 received reversed index492
receiver caught ball @ shotclock: 15.69 @ gametime 379.58 received reversed index493
[8.6819, 25.79634]
d

...

Finding correct SportVU eventNum for gameid:0021500078
curr eventNum:241 , prev eventNum:None
Currently checking eventNumPBP: 241
sportVU Index for the eventNumPBP: 202
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:223 with SportsVU moment game clock:190.78
curr eventNum:240 , prev eventNum:None
Currently checking eventNumPBP: 240
sportVU Index for the eventNumPBP: 201
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:223 with SportsVU moment game clock:197.78
curr eventNum:239 , prev eventNum:None
Currently checking eventNumPBP: 239
Could not find moments for this eventNum in SportsVU: 239
Could not find eventNum in SportsVU 

prevGameID:21500078, currentlyAnalyzingGameID:21500078
PBPEventNum:285, gametimePBP:0:17
Finding correct SportVU eventNum for gameid:0021500078
curr eventNum:285 , prev eventNum:None
Currently checking eventNumPBP: 285
sportVU Index for the eventNumPBP: 237
Could not find moments f

Finding correct SportVU eventNum for gameid:0021500082
curr eventNum:283 , prev eventNum:None
Currently checking eventNumPBP: 283
sportVU Index for the eventNumPBP: 248
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:546 with SportsVU moment game clock:534.0
curr eventNum:282 , prev eventNum:None
Currently checking eventNumPBP: 282
sportVU Index for the eventNumPBP: 247
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:546 with SportsVU moment game clock:551.81
Corrected eventNum to be searching for in SportsVU: 282
Correct SportVU eventNum: 282
receiverID = 203083 , passerID = 202704
Drummond  Alley Oop Dunk (7 PTS) (Jackson 6 AST)
num of moments: 552
starting at time: 546.02with total momentList length of 552
receiver holding ball @ shotclock: 15.76 @ gametime 548.97
receiver holding ball @ shotclock: 15.8 @ gametime 549.01
receiver holding ball @ shotclock: 15.84 @ gametime 549.05
receiver caught ball @ 

Finding correct SportVU eventNum for gameid:0021500089
curr eventNum:303 , prev eventNum:None
Currently checking eventNumPBP: 303
sportVU Index for the eventNumPBP: 265
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:313 with SportsVU moment game clock:310.0
curr eventNum:302 , prev eventNum:None
Currently checking eventNumPBP: 302
sportVU Index for the eventNumPBP: 264
Comparing Target PBP quarter:3 , with  SportVU quarter :3
Comparing Target PBP gameclock:313 with SportsVU moment game clock:310.0
curr eventNum:301 , prev eventNum:None
Currently checking eventNumPBP: 301
sportVU Index for the eventNumPBP: 263
Could not find moments for this eventNum in SportsVU: 301
Could not find eventNum in SportsVU 

prevGameID:21500089, currentlyAnalyzingGameID:21500089
PBPEventNum:386, gametimePBP:9:34
Finding correct SportVU eventNum for gameid:0021500089
curr eventNum:386 , prev eventNum:None
Currently checking eventNumPBP: 386
sportVU Index for the even

Finding correct SportVU eventNum for gameid:0021500094
curr eventNum:126 , prev eventNum:None
Currently checking eventNumPBP: 126
sportVU Index for the eventNumPBP: 111
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:54 with SportsVU moment game clock:67.46
Corrected eventNum to be searching for in SportsVU: 126
Correct SportVU eventNum: 126
receiverID = 202684 , passerID = 203521
Thompson  Alley Oop Dunk (4 PTS) (Dellavedova 2 AST)
num of moments: 402
starting at time: 54.9with total momentList length of 402
receiver holding ball @ shotclock: 24.0 @ gametime 54.9
receiver holding ball @ shotclock: 24.0 @ gametime 54.9
receiver holding ball @ shotclock: 24.0 @ gametime 54.9
receiver caught ball @ shotclock: 15.1 @ gametime 55.7 received reversed index107
receiver caught ball @ shotclock: 15.14 @ gametime 55.74 received reversed index108
receiver caught ball @ shotclock: 15.18 @ gametime 55.78 received reversed index109
[83.00663, 26.92418]
defen

Finding correct SportVU eventNum for gameid:0021500097
curr eventNum:35 , prev eventNum:None
Currently checking eventNumPBP: 35
sportVU Index for the eventNumPBP: 31
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:520 with SportsVU moment game clock:528.92
Corrected eventNum to be searching for in SportsVU: 35
Correct SportVU eventNum: 35
receiverID = 203460 , passerID = 201566
Roberson  Alley Oop Dunk (2 PTS) (Westbrook 1 AST)
num of moments: 250
starting at time: 520.02with total momentList length of 250
receiver holding ball @ shotclock: 20.64 @ gametime 522.67
receiver holding ball @ shotclock: 20.68 @ gametime 522.71
receiver holding ball @ shotclock: 20.73 @ gametime 522.75
receiver caught ball @ shotclock: 21.33 @ gametime 523.27 received reversed index108
receiver caught ball @ shotclock: 21.38 @ gametime 523.31 received reversed index109
receiver caught ball @ shotclock: 21.43 @ gametime 523.35 received reversed index110
[82.25252, 29.6

## Mining each turnover event 

In [130]:
print("Starting unparsed pass dataset: "+ str(len(BadPass_df)))
CleanData_df = pd.DataFrame(columns=['GameID', 'Period', 'SportVUeventNum', 'SportVUMomentIndex', 'reversedIndexBallCaught', 'PBPGameTime' , 'timeballpassed','timeballcaught', 'ShotClock', 'PasserID', 'ReceiverID', 'PassDist',  'passInHull', 'receiverinHull', 'HullArea','receiverIsOpen' , 'PBP_HOMEDESCRIPTION' , 'PBP_VISITORDESCRIPTION', 'rawMoments', 'defensivePositions', 'isAlleyOOp', 'Success'])
momentsJson_df = pd.DataFrame(columns=['jsonMoments'])
if(not curPath.endswith('SportVU_JSON_Data')):
    curPath = os.getcwd()
    print curPath
    strIndex=curPath.index('\\JupyterNotebooks\\')
    curPath = curPath[:(strIndex+18)]+'SportVU_JSON_Data\\'
    os.chdir(curPath)
print curPath
#SportVU_JSON_Rootpath = "C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\\"
#print SportVU_JSON_Rootpath+str(gameid)+".json"
gameid_prev = 0;
for index, to in BadPass_df.iterrows():
    gameid = to["GAME_ID"]    #game id from PBP
    eventNumPBP = to["EVENTNUM"] #eventNumber for the play
    gametimePBP = to["PCTIMESTRING"]  #game time for the play
    quarterPBP = int(to["PERIOD"])
    #getPBPInfo(gameid,eventNumPBP)
    print("prevGameID:"+str(gameid_prev)+", currentlyAnalyzingGameID:"+str(gameid))
    print("PBPEventNum:"+str(eventNumPBP)+", gametimePBP:"+str(gametimePBP))
    #check if SportVU json data is already opened for this PBP play
    if(gameid_prev != gameid):
        #open raw JSON SportVU data using game id from assist
        with open(curPath+"00"+str(gameid)+".json") as data_file:    
            rawSportVUData = json.load(data_file)
            json_normalize(rawSportVUData['events'])
        gameid_prev = gameid
    
    #get the correct eventNum (returned as long) in SportsVU
    eventNumSportsVU, rawpossessionSportsVU = findCorrectMomentData(rawSportVUData, quarterPBP, gametimePBP, eventNumPBP)
    if(eventNumSportsVU is None):
        print("Could not find eventNum in SportsVU \n")
        continue
    
    print("Correct SportVU eventNum: "+str(eventNumSportsVU))
    #extract SportsVU movements for that eventNum
    
    rawpossessionSportsVU = MomentsfromEventNum(rawSportVUData, int(eventNumSportsVU))
    
    #for analyzing OOP only...
    receiverID = int(to['PLAYER2_ID'])  
    passerID = int(to['PLAYER1_ID'])
    teamID = int(to['PLAYER1_TEAM_ID'])
    if(math.isnan(to['PLAYER2_TEAM_ID'])):
        if (rawSportVUData['events'][0]['home']['teamid'] == teamID ):
            print("defense team: "+rawSportVUData['events'][0]['visitor']['name']);
            defenseTeamId =  rawSportVUData['events'][0]['visitor']['teamid'];
        else:
            defenseTeamId =  rawSportVUData['events'][0]['home']['teamid'];
            print("defense team: "+rawSportVUData['events'][0]['home']['name']);  
    else:
        defenseTeamId = int(to['PLAYER2_TEAM_ID'])
                 
    
    #PBPTime = str(oop['PCTIMESTRING'])
    PBP_HOMEDESCRIPTION = str(to['HOMEDESCRIPTION']) 
    PBP_VISITORDESCRIPTION = str(to['VISITORDESCRIPTION'])
    
                     
    #get catch details (who was the passer, receiver, and when caught/passed)
    timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass , SportVUMomentIndex= getTOEventDetails(receiverID, passerID, defenseTeamId, gametimePBP, rawpossessionSportsVU)
    
    if(timeBallReleased is None):
        print("Could not find time for when ball was passed")
        continue
    
    #hull details
    momentsReversed = rawpossessionSportsVU[::-1]
    

        
    hull, defensive_positions = getHull(momentsReversed[indexBallCaught], defenseTeamId)
    
    #Defensive Hull Area
    hullArea = hull.area
    
    #passer in hull?
    passerInHull = isInHull(hull,defensive_positions, passerPosAtPass[0] ,passerPosAtPass[1])
                     
    #receiver in hull?
    receiverInHull = isInHull(hull,defensive_positions, receiverPosAtPass[0] ,receiverPosAtPass[1])
      
    #is receiver open?  ( np_points position of defense)
    closestDist, receiverIsOpen = is_open([receiverPosAtCaught[0],receiverPosAtCaught[1]], defensive_positions)
    
    #pass Distance
    passDist =distance.euclidean(passerPosAtPass,receiverPosAtCaught)
    
    #shot clock time
    shotClockTime = momentsReversed[indexBallPassed][3]
    
    rawMoments =  momentsReversed[indexBallCaught:indexBallPassed]
    #unreverse moments
    rawMoments = rawMoments[::-1]
    
#    allmoments=[]
#    for moment in rawMoments:
#        jsonMoment = moments2JSON(moment)
#        allmoments.append(jsonMoment)
#   jsonMoments = ",".join(allmoments)
#    jsonMoments = "{ \"moments\":["+jsonMoments+"]}"
    
    
    isAlleyOop = False;
    isSuccess = False;
    
    #PBPTime , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION = getPBPInfo("00"+str(gameid), eventNumPBP) 
    CleanData_df.loc[len(CleanData_df.index)] = [gameid, quarterPBP, eventNumSportsVU, SportVUMomentIndex , indexBallCaught, gametimePBP, timeBallPassed, timeBallCaught, shotClockTime, passerID, receiverID , passDist, passerInHull, receiverInHull, hullArea, receiverIsOpen  , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION, rawMoments, defensive_positions, isAlleyOop,  isSuccess]
    #momentsJson_df.loc[len(momentsJson_df.index)] = [jsonMoments]
    
CleanData_df.to_csv("CleanedDataTO_.csv", sep=',')
#momentsJson_df.to_csv("momentdataonly.csv", sep=' ', index=False, header=False)


Starting unparsed pass dataset: 1320
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\
prevGameID:0, currentlyAnalyzingGameID:21500001
PBPEventNum:4, gametimePBP:11:37
Finding correct SportVU eventNum for gameid:0021500001
curr eventNum:4 , prev eventNum:None
Currently checking eventNumPBP: 4
sportVU Index for the eventNumPBP: 3
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:697 with SportsVU moment game clock:702.12
Corrected eventNum to be searching for in SportsVU: 4
Correct SportVU eventNum: 4
sportVU Index for the eventNumPBP: 3
defense team: Detroit Pistons
num of moments: 128
starting at time: 697.02
Defensive positions: [[88.36494, 22.74693], [71.11962, 22.07787], [76.08034, 34.92503], [79.84997, 10.39164], [83.70311, 21.02741]]
prevGameID:21500001, currentlyAnalyz

Finding correct SportVU eventNum for gameid:0021500003
curr eventNum:12 , prev eventNum:None
Currently checking eventNumPBP: 12
sportVU Index for the eventNumPBP: 11
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:607 with SportsVU moment game clock:615.68
Corrected eventNum to be searching for in SportsVU: 12
Correct SportVU eventNum: 12
sportVU Index for the eventNumPBP: 11
defense team: New Orleans Pelicans
num of moments: 341
starting at time: 607.05
Defensive positions: [[16.64937, 5.6312], [37.03974, 19.78246], [6.29814, 12.39849], [64.45315, 6.35885], [56.59472, 23.25218]]
prevGameID:21500003, currentlyAnalyzingGameID:21500003
PBPEventNum:35, gametimePBP:7:17
Finding correct SportVU eventNum for gameid:0021500003
curr eventNum:35 , prev eventNum:None
Currently checking eventNumPBP: 35
sportVU Index for the eventNumPBP: 34
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:437 with SportsVU moment game

Finding correct SportVU eventNum for gameid:0021500004
curr eventNum:2 , prev eventNum:None
Currently checking eventNumPBP: 2
sportVU Index for the eventNumPBP: 1
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:701 with SportsVU moment game clock:708.95
Corrected eventNum to be searching for in SportsVU: 2
Correct SportVU eventNum: 2
sportVU Index for the eventNumPBP: 1
defense team: Orlando Magic
num of moments: 470
starting at time: 701.03
Defensive positions: [[88.63828, 33.47115], [74.82819, 17.58505], [38.71203, 3.65165], [32.4858, 6.26314], [77.13436, 45.64856]]
prevGameID:21500004, currentlyAnalyzingGameID:21500004
PBPEventNum:8, gametimePBP:10:48
Finding correct SportVU eventNum for gameid:0021500004
curr eventNum:8 , prev eventNum:None
Currently checking eventNumPBP: 8
sportVU Index for the eventNumPBP: 6
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:648 with SportsVU moment game clock:648.0
Co

Finding correct SportVU eventNum for gameid:0021500005
curr eventNum:27 , prev eventNum:None
Currently checking eventNumPBP: 27
sportVU Index for the eventNumPBP: 22
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:567 with SportsVU moment game clock:579.0
Corrected eventNum to be searching for in SportsVU: 27
Correct SportVU eventNum: 27
sportVU Index for the eventNumPBP: 22
num of moments: 575
starting at time: 567.0
Defensive positions: [[60.9383, 21.2356], [31.94172, 38.94581], [17.76019, 19.08797], [9.93687, 17.7047], [45.93874, 27.59952]]
prevGameID:21500005, currentlyAnalyzingGameID:21500005
PBPEventNum:83, gametimePBP:3:22
Finding correct SportVU eventNum for gameid:0021500005
curr eventNum:83 , prev eventNum:None
Currently checking eventNumPBP: 83
sportVU Index for the eventNumPBP: 73
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:202 with SportsVU moment game clock:208.42
Corrected eventNum to b

Finding correct SportVU eventNum for gameid:0021500007
curr eventNum:8 , prev eventNum:None
Currently checking eventNumPBP: 8
sportVU Index for the eventNumPBP: 7
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:647 with SportsVU moment game clock:661.04
Corrected eventNum to be searching for in SportsVU: 8
Correct SportVU eventNum: 8
sportVU Index for the eventNumPBP: 7
defense team: Detroit Pistons
num of moments: 666
starting at time: 647.01
Defensive positions: [[20.04332, 29.33973], [83.94822, 23.99354], [91.9634, 15.01345], [3.92554, 49.52413], [19.16854, 18.91528]]
prevGameID:21500007, currentlyAnalyzingGameID:21500007
PBPEventNum:32, gametimePBP:6:57
Finding correct SportVU eventNum for gameid:0021500007
curr eventNum:32 , prev eventNum:None
Currently checking eventNumPBP: 32
sportVU Index for the eventNumPBP: 31
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:417 with SportsVU moment game clock:42

...

Finding correct SportVU eventNum for gameid:0021500093
curr eventNum:10 , prev eventNum:None
Currently checking eventNumPBP: 10
sportVU Index for the eventNumPBP: 7
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:657 with SportsVU moment game clock:662.14
Corrected eventNum to be searching for in SportsVU: 10
Correct SportVU eventNum: 10
sportVU Index for the eventNumPBP: 7
num of moments: 625
starting at time: 657.0
Defensive positions: [[87.20917, 14.11986], [62.46157, 35.16519], [87.38471, 30.98407], [78.84777, 41.96953], [85.60623, 29.09172]]
prevGameID:21500093, currentlyAnalyzingGameID:21500093
PBPEventNum:36, gametimePBP:8:47
Finding correct SportVU eventNum for gameid:0021500093
curr eventNum:36 , prev eventNum:None
Currently checking eventNumPBP: 36
sportVU Index for the eventNumPBP: 29
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:527 with SportsVU moment game clock:527.58
Corrected eventNum t

Finding correct SportVU eventNum for gameid:0021500095
curr eventNum:55 , prev eventNum:None
Currently checking eventNumPBP: 55
sportVU Index for the eventNumPBP: 50
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:386 with SportsVU moment game clock:395.0
Corrected eventNum to be searching for in SportsVU: 55
Correct SportVU eventNum: 55
sportVU Index for the eventNumPBP: 50
num of moments: 400
starting at time: 386.03
Defensive positions: [[62.13638, 27.95418], [82.85994, 37.81468], [76.03621, 13.82268], [77.40104, 26.04605], [49.45882, 21.88248]]
prevGameID:21500095, currentlyAnalyzingGameID:21500095
PBPEventNum:136, gametimePBP:1:04
Finding correct SportVU eventNum for gameid:0021500095
curr eventNum:136 , prev eventNum:None
Currently checking eventNumPBP: 136
sportVU Index for the eventNumPBP: 118
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:64 with SportsVU moment game clock:80.61
Corrected eventN

Finding correct SportVU eventNum for gameid:0021500097
curr eventNum:26 , prev eventNum:None
Currently checking eventNumPBP: 26
sportVU Index for the eventNumPBP: 22
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:573 with SportsVU moment game clock:583.0
Corrected eventNum to be searching for in SportsVU: 26
Correct SportVU eventNum: 26
sportVU Index for the eventNumPBP: 22
num of moments: 425
starting at time: 573.01
Defensive positions: [[39.53995, 10.41344], [41.65951, 34.11676], [34.06805, 23.56319], [21.77487, 20.48662], [14.13105, 26.94627]]
prevGameID:21500097, currentlyAnalyzingGameID:21500097
PBPEventNum:34, gametimePBP:8:45
Finding correct SportVU eventNum for gameid:0021500097
curr eventNum:34 , prev eventNum:None
Currently checking eventNumPBP: 34
sportVU Index for the eventNumPBP: 30
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:525 with SportsVU moment game clock:531.0
Corrected eventNum 

Finding correct SportVU eventNum for gameid:0021500098
curr eventNum:153 , prev eventNum:None
Currently checking eventNumPBP: 153
sportVU Index for the eventNumPBP: 132
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:554 with SportsVU moment game clock:570.7
Corrected eventNum to be searching for in SportsVU: 153
Correct SportVU eventNum: 153
sportVU Index for the eventNumPBP: 132
num of moments: 525
starting at time: 554.02
Defensive positions: [[38.82596, 40.83933], [22.5931, 15.62581], [9.85749, 26.75829], [17.42576, 40.11792], [33.47146, 4.82534]]
prevGameID:21500098, currentlyAnalyzingGameID:21500098
PBPEventNum:176, gametimePBP:6:08
Finding correct SportVU eventNum for gameid:0021500098
curr eventNum:176 , prev eventNum:None
Currently checking eventNumPBP: 176
sportVU Index for the eventNumPBP: 154
Comparing Target PBP quarter:2 , with  SportVU quarter :2
Comparing Target PBP gameclock:368 with SportsVU moment game clock:374.32
Corrected e

Finding correct SportVU eventNum for gameid:0021500099
curr eventNum:39 , prev eventNum:None
Currently checking eventNumPBP: 39
sportVU Index for the eventNumPBP: 35
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:430 with SportsVU moment game clock:441.48
Corrected eventNum to be searching for in SportsVU: 39
Correct SportVU eventNum: 39
sportVU Index for the eventNumPBP: 35
num of moments: 675
starting at time: 430.03
Defensive positions: [[47.32181, 28.2823], [64.34733, 40.95472], [18.99311, 25.48453], [13.20286, 24.7787], [26.38888, 21.71668]]
prevGameID:21500099, currentlyAnalyzingGameID:21500099
PBPEventNum:43, gametimePBP:6:38
Finding correct SportVU eventNum for gameid:0021500099
curr eventNum:43 , prev eventNum:None
Currently checking eventNumPBP: 43
sportVU Index for the eventNumPBP: 39
Comparing Target PBP quarter:1 , with  SportVU quarter :1
Comparing Target PBP gameclock:398 with SportsVU moment game clock:407.44
Corrected eventNum 

## UNITY pipeline for datavisualization

In [ ]:
# for each assist event .... (FOR UNITY Data Visualizer)
print("Starting unparsed pass dataset: "+ str(len(AST_df)))
CleanData_df = pd.DataFrame(columns=['GameID', 'Period', 'SportVUeventNum', 'SportVUMomentIndex', 'reversedIndexBallCaught', 'PBPGameTime' , 'timeballpassed','timeballcaught', 'ShotClock', 'PasserID', 'ReceiverID', 'PassDist',  'passInHull', 'receiverinHull', 'HullArea','receiverIsOpen' , 'PBP_HOMEDESCRIPTION' , 'PBP_VISITORDESCRIPTION', 'rawMoments', 'jsonMoments'])
momentsJson_df = pd.DataFrame(columns=['jsonMoments'])
if(not curPath.endswith('SportVU_JSON_Data')):
    curPath = os.getcwd()
    print curPath
    strIndex=curPath.index('\\JupyterNotebooks\\')
    curPath = curPath[:(strIndex+18)]+'SportVU_JSON_Data\\'
    os.chdir(curPath)
print curPath
#SportVU_JSON_Rootpath = "C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data\\"
#print SportVU_JSON_Rootpath+str(gameid)+".json"
gameid_prev = 0;
for index, ast in AST_df.iterrows():
    gameid = ast["GAME_ID"]    #game id from PBP
    eventNumPBP = ast["EVENTNUM"] #eventNumber for the play
    gametimePBP = ast["PCTIMESTRING"]  #game time for the play
    quarterPBP = int(ast["PERIOD"])
    #getPBPInfo(gameid,eventNumPBP)
    print("prevGameID:"+str(gameid_prev)+", currentlyAnalyzingGameID:"+str(gameid))
    print("PBPEventNum:"+str(eventNumPBP)+", gametimePBP:"+str(gametimePBP))
    #check if SportVU json data is already opened for this PBP play
    if(gameid_prev != gameid):
        #open raw JSON SportVU data using game id from assist
        with open(curPath+"00"+str(gameid)+".json") as data_file:    
            rawSportVUData = json.load(data_file)
            json_normalize(rawSportVUData['events'])
        gameid_prev = gameid
    
    #get the correct eventNum (returned as long) in SportsVU
    eventNumSportsVU = findCorrectMomentData(rawSportVUData, quarterPBP, gametimePBP, eventNumPBP)
    if(eventNumSportsVU is None):
        print("Could not find eventNum in SportsVU")
        continue
    
    
    print("Correct SportVU eventNum: "+str(eventNumSportsVU))
    #extract SportsVU movements for that eventNum
    
    rawpossessionSportsVU = MomentsfromEventNum(rawSportVUData, int(eventNumSportsVU))
    
    #for analyzing AST only...
    receiverID = int(ast['PLAYER1_ID'])
    passerID = int(ast['PLAYER2_ID'])
    teamID = int(ast['PLAYER1_TEAM_ID'])
    #PBPTime = str(ast['PCTIMESTRING'])
    PBP_HOMEDESCRIPTION = str(ast['HOMEDESCRIPTION']) 
    PBP_VISITORDESCRIPTION = str(ast['VISITORDESCRIPTION'])
    
                     
    #get catch details (who was the passer, receiver, and when caught/passed)
    timeBallReleased, indexBallReleased, timeBallCaught, indexBallCaught, timeBallPassed, indexBallPassed, receiverPosAtPass, receiverPosAtCaught, passerPosAtPass , SportVUMomentIndex= getCatchEventDetails(receiverID, passerID, gametimePBP, rawpossessionSportsVU)
    
    if(timeBallReleased is None):
        print("Could not find time for when ball was passed")
        continue
    
    #hull details
    momentsReversed = rawpossessionSportsVU[::-1]
    
    if (rawSportVUData['events'][0]['home']['teamid'] == teamID ):
        print("defense team: "+rawSportVUData['events'][0]['visitor']['name']);
        defenseTeamId =  rawSportVUData['events'][0]['visitor']['teamid'];
    else:
        defenseTeamId =  rawSportVUData['events'][0]['home']['teamid'];
        print("defense team: "+rawSportVUData['events'][0]['home']['name']);
    hull, np_points = getHull(momentsReversed[indexBallCaught], defenseTeamId)
    
    #Defensive Hull Area
    hullArea = hull.area
    
    #passer in hull?
    passerInHull = isInHull(hull,np_points, passerPosAtPass[0] ,passerPosAtPass[1])
                     
    #receiver in hull?
    receiverInHull = isInHull(hull,np_points, receiverPosAtPass[0] ,receiverPosAtPass[1])
      
    #is receiver open?  ( np_points position of defense)
    closestDist, receiverIsOpen = is_open([receiverPosAtCaught[0],receiverPosAtCaught[1]], np_points)
    
    #pass Distance
    passDist =distance.euclidean(passerPosAtPass,receiverPosAtCaught)
    
    #shot clock time
    shotClockTime = momentsReversed[indexBallPassed][3]
    
    rawMoments =  momentsReversed[indexBallCaught:indexBallPassed]
    #unreverse moments
    rawMoments = rawMoments[::-1]
    
    allmoments=[]
    for moment in rawMoments:
        jsonMoment = moments2JSON(moment)
        allmoments.append(jsonMoment)
    jsonMoments = ",".join(allmoments)
    jsonMoments = "{ \"moments\":["+jsonMoments+"]}"
    
    
    #PBPTime , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION = getPBPInfo("00"+str(gameid), eventNumPBP) 
    CleanData_df.loc[len(CleanData_df.index)] = [gameid, quarterPBP, eventNumSportsVU, SportVUMomentIndex , indexBallCaught, gametimePBP, timeBallPassed, timeBallCaught, shotClockTime, passerID, receiverID , passDist, passerInHull, receiverInHull, hullArea, receiverIsOpen  , PBP_HOMEDESCRIPTION , PBP_VISITORDESCRIPTION, rawMoments, jsonMoments ]
    momentsJson_df.loc[len(momentsJson_df.index)] = [jsonMoments]
    
CleanData_df.to_csv("CleanedData.csv", sep=',')
momentsJson_df.to_csv("momentdataonly.csv", sep=' ', index=False, header=False)


In [ ]:
len(momentsReversed[1][5])

In [60]:
getPBPInfo(21500101,8)

C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\SportVU_JSON_Data
C:\Users\jchin\Documents\GitHub\Data Mining Course\DataMining-Project-Folder\JupyterNotebooks\\pbp-csv
8    10:56
Name: PCTIMESTRING, dtype: object
8    Teague 1' Cutting Layup Shot (2 PTS) (Millsap ...
Name: HOMEDESCRIPTION, dtype: object
8    NaN
Name: VISITORDESCRIPTION, dtype: object


(8    10:56
 Name: PCTIMESTRING, dtype: object,
 8    Teague 1' Cutting Layup Shot (2 PTS) (Millsap ...
 Name: HOMEDESCRIPTION, dtype: object,
 8    NaN
 Name: VISITORDESCRIPTION, dtype: object)

In [ ]:
shooter_loc = [77.77774, 25.25539]
#def_locs = [(56.27694, 25.51460), (73.64107, 25.48774), (48.6492, 35.26915), (48.46352, 14.55436), (47.51449, 24.36448)]
def_locs = [[72.01085, 22.81862], [89.8139, 33.73649], [71.96631, 28.4613], [79.33885, 47.77566], [70.85107, 6.3982]]
print(is_open(shooter_loc, def_locs))




BadPass_df.iloc[0]

In [64]:
GameTimetoSeconds("10:56")

656


656